In [ ]:
!pip -q install git+https://github.com/huggingface/transformers.git
!pip -q install peft
!pip -q install accelerate
!pip -q install sentencepiece
!pip -q install bitsandbytes

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 9.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 114.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.3/40.3 kB 6.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.3/215.3 kB 24.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 65.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.3/104.3 MB 9.6 MB/s eta 0:00:00


In [ ]:
from IPython.display import Markdown as md

import transformers
import peft
import accelerate
import bitsandbytes

print(transformers.__version__)
print(peft.__version__)
print(accelerate.__version__)



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so.11.0
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so...


/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: /usr/lib64-nvidia did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('8013'), PosixPath('http'), PosixPath('//172.28.0.1')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('--logtostderr --listen_host=172.28.0.12 --

4.29.0.dev0
0.2.0
0.18.0


In [6]:
import torch
from peft import PeftModel
from transformers import LlamaTokenizer, LlamaForCausalLM

def load_model(base, finetuned):
    tokenizer = LlamaTokenizer.from_pretrained(base)
    tokenizer.pad_token_id = 0
    tokenizer.padding_side = "left"

    model = LlamaForCausalLM.from_pretrained(
        base,
        load_in_8bit=True,
        device_map="auto",
    )
    
    model = PeftModel.from_pretrained(
        model, 
        finetuned,
        device_map={'': 0}
    )
    return model, tokenizer

def get_output_batch(
    model, tokenizer, prompt, generation_config, device='cuda'
):
  encoding = tokenizer(prompt, return_tensors="pt")
  input_ids = encoding["input_ids"].to(device)
  generated_id = model.generate(
      input_ids=input_ids,
      generation_config=generation_config,
      max_new_tokens=256
  )

  decoded = tokenizer.batch_decode(
      generated_id, skip_prompt=True, skip_special_tokens=True
  )
  del input_ids, generated_id
  torch.cuda.empty_cache()
  return decoded[0].split("### Response:")[-1]

### Alpaca-LoRA 13B (05/01)

In [14]:
from transformers import GenerationConfig

base = "elinas/llama-13b-hf-transformers-4.29"
sft = "LLMs/Alpaca-LoRA-13B-elina"

genConfig = GenerationConfig(
    temperature=0.95,
    top_p=0.9,
    top_k=50,
    num_beams=1,
    repetition_penalty=1.2,
    max_new_token=2048,
    do_sample=True,
)

In [5]:
model, tokenizer = load_model(base, sft)

Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

In [15]:
prompt = """### Instruction: Compose an engaging travel blog post about a recent trip to Hawaii, highlighting cultural experiences and must-see attractions.

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 The beauty of the islands in Hawaii is truly captivating. From stunning volcanoes like Kilauea, waterfalls tumbling into clear pools like Rainbow Falls, breathtaking coastal vistas like Hanauma Bay Beach Park, and lush tropical rainforests brimming with wildlife such as monk seals and green sea turtles - there's so much more than sandy beaches and palm trees! <br /><br />I recently had the opportunity to explore several different sides of this unique destination during my visit last summer. I went snorkeling off the Big Island’s eastern shoreline near Punaluʻu Black Sand beach where it was easy to spot dozens of colorful fish amongst black lava rock formations. On Maui, we explored Haleakala National park for hiking opportunities amidst bamboo groves, bright blue skies and flourishing mountain scenery. Finally on Oahu, my group enjoyed surfing at Waimea Bay - one of the most popular surf spots along North Shore.

In [16]:
prompt = """### Instruction: Can you help me write a formal email to a potential business partner proposing a joint venture?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 <br />Dear [Name],  <br />I am writing today in hopes of discussing the possibility for collaboration with your company. I believe our services can compliment each other and offer mutual benefits that would enable us both to grow as successful entities within this marketplace. We have some unique ideas which we feel could create synergy between companies, allowing us to expand our presence in existing markets while providing new opportunities into untapped territories. As such, we are interested in exploring the opportunity to work together on an equal partnership basis. If it is convenient for you, please let us know if there may be time to meet or talk further about these prospects over the phone. Looking forward to hearing from you soon!

In [17]:
prompt = """### Instruction: Can you help me write a resignation letter to my current employer, while leaving on good terms and expressing gratitude for the opportunities provided?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Dear [Name of Employer], <br /><br />It is with great sadness that I am writing this note to inform you that after careful consideration I have decided it’s time for me to move on from [Company Name]. This decision was not easy but after much thought I believe it's best both personally and professionally. My tenure at [Organization] has been an amazingly rewarding experience and one which will always be remembered fondly by myself and all those who have worked alongside me.<br />I would like thank you for your support throughout these past years and look forward to stay in contact during our new journeys!

In [18]:
prompt = """### Instruction: How can you determine if a restaurant is popular among locals or mainly attracts tourists, and why might this information be useful?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 To understand the distinction between local restaurants vs. touristy restaurants, one could look at reviews on sites such as TripAdvisor to see which establishments receive higher ratings from residents of that area versus visitors there for just a day or two. A more direct approach would involve asking those who live in the city how often they visit certain places and what their opinion of them is compared with other eateries in town. This kind of insight into where people dine most frequently will help someone discover whether a particular eatery primarily caters to long-time inhabitants or short-term travelers. Additionally, knowing an establishment's clientele can aid in understanding its menu offerings (if it has any specialty items) and ambiance. Furthermore, being aware of what type of customers frequent the place may allow one to anticipate when and by whom the restaurant experiences peak periods of activity, helping individuals make plans accordingly.

In [19]:
prompt = """### Instruction: What are some subtle clues that suggest someone is pretending to understand a topic or conversation when they are actually confused or uninformed?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Some of the hints can include using too many long, convoluted words instead of simple ones, relying on jargon without fully understanding it themselves. They might also use filler words like "uh" and hesitate before giving an answer - suggesting their response is not based on knowledge but more from instinctive guesses and assumptions.

In [20]:
prompt = """### Instruction: What are some potential implications of using a single-use plastic bottle versus a reusable bottle on both the environment and human health?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 <br />Using single use plastics has many negative impacts. Plastic is not easily biodegradable, so it stays in landfills for decades and can cause environmental contamination when exposed to sunlight or other elements. It also takes hundreds of years before plastic decomposes into organic matter, which means that any resources used to produce these plastic items have been wasted over time due to their lack of recyclability. In addition, single use plastics create pollution through leaching chemicals such as bisphenol A (BPA) into waterways and oceans where animals ingest them with disastrous effects on their own ecosystem. On top of this, burning fossil fuels produces greenhouse gases responsible for global warming, making plastic production an even more unsustainable practice.<br />By contrast, the use of reusable materials such as glass and metal reduces waste from disposables while promoting sustainability by extending product life cycles. Reusables typically require fewer energy inputs during manufacturing and production than do most forms of plastic because they often last longer. These products can be collected and transported safely without causing significant harm to our ecological system either

In [21]:
prompt = """### Instruction: What factors would you consider when designing an inclusive and accessible public transportation system?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 When designing a comprehensive, inclusive, and accessible transit network, there are several key aspects to take into consideration. Firstly, the size of a city is critical in determining what type of transit will be most suitable for its inhabitants; larger cities may benefit from subway or tram systems while smaller ones can use buses, shuttles, light rail, streetcars, ferries, bicycles, scooters, etc. Secondly, it’s important to look at accessibility – whether people with disabilities have equal access to the services provided by such networks must also be considered. Thirdly, the costs involved need to be assessed so that users feel they are receiving value for their money. Additionally, safety standards should be high enough to ensure that passengers do not face any threats onboard trains and other modes of mass transit. Finally, environmental sustainability has become increasingly crucial as concerns about climate change grow louder, thus eco-friendliness needs to play a major role in the development process of a robust public transportation system.